In [1]:
import os
import zipfile
%load_ext autoreload

%autoreload 2

In [2]:
import tracemalloc
import psutil
import pprint
import pandas as pd
import uuid
import json
import os
import glob
import re
import sys
from bs4 import NavigableString, BeautifulSoup
from collections import defaultdict
import random
import string
import time

from utils.config import config
from utils.logger.logger import loggerCreator

# ePI Modules
from parse.rulebook.rulebook import StyleRulesDictionary

from parse.extractor.parser import parserExtractor
from match.matchDocument.matchDocument import MatchDocument
from documentAnnotation.documentAnnotation import DocumentAnnotation
from htmlDocTypePartitioner.partition import DocTypePartitioner
from extractContentBetweenHeadings.dataBetweenHeadingsExtractor import DataBetweenHeadingsExtractor
from fhirXmlGenerator.fhirXmlGenerator import FhirXmlGenerator
from fhirService.fhirService import FhirService
from utils.logger.matchLogger import MatchLogger
from languageInfo.documentTypeNames.documentTypeNames import DocumentTypeNames
from wordToHtmlConvertor.wordToHtmlConvertor import WordToHtmlConvertor


class FolderNotFoundError(Exception):
    pass

class Metrics:
    
    def __init__(self, logFileName, logger):
        self.logFileName = logFileName
        self.start()
        self.writer = open(self.logFileName, 'a')
        self.writer.write("StepName,Time,Current Memory,Peak Memory,Used Ram Percentage\n")
        self.finalPeak = 0
        self.finalTotalTime = 0
        self.finalUsedRamPerc = 0
        self.logger = logger
    
    def start(self):
        self.startTime = time.time()
        tracemalloc.start()
    
    def getMetric(self, msg):
        
        self.endTime = time.time()
        
        self.totalTime = round((self.endTime - self.startTime)/60,3)
        
        
        current, peak = tracemalloc.get_traced_memory()
        current = current / 10**6
        peak = peak / 10**6
        
        usedRamPerc = psutil.virtual_memory()[2]
        
        self.finalPeak = max(self.finalPeak, peak)
        self.finalUsedRamPerc = max(self.finalUsedRamPerc, usedRamPerc)

        self.finalTotalTime = self.finalTotalTime + self.totalTime
        self.finalTotalTime = round(self.finalTotalTime/60,3)
        
        outputString = f"{msg},{self.totalTime} Min,{current} MB,{peak} MB,{usedRamPerc}\n"
        
        self.logger.logFlowCheckpoint(f"{outputString}")
        
        print(f"Metrics : {outputString}")
        self.writer.write(outputString)
        tracemalloc.stop()
        tracemalloc.start()
        self.startTime = time.time()
    def end(self):
        
        current, peak = tracemalloc.get_traced_memory()
        current = current / 10**6
        outputString = f"Final Metrics,{self.finalTotalTime} Min,{current} MB,{self.finalPeak} MB,{self.finalUsedRamPerc}\n"
        print(f"Metrics : {outputString}")
        self.logger.logFlowCheckpoint(f"{outputString}")
        self.finalTotalTime.write(outputString)
        self.writer.close()
        tracemalloc.stop()
        
        


def convertToInt(x):
    try:
        return str(int(x))
    except:
        return x


def convertCollectionToDataFrame(collection):

    dfExtractedHier = pd.DataFrame(collection)
    dfExtractedHier['parent_id'] = dfExtractedHier['parent_id'].apply(
        lambda x: convertToInt(x))
    dfExtractedHier['id'] = dfExtractedHier['id'].apply(
        lambda x: convertToInt(x))

    return dfExtractedHier

def getRandomString(N):
    str_ = ''.join(random.choice(string.ascii_uppercase + string.digits
                                 + string.ascii_lowercase) for _ in range(N))
    return str_


def convertHtmlToJson(controlBasePath, basePath, domain, procedureType, languageCode, htmlDocName, fileNameQrd, fileNameLog):

    module_path = os.path.join(basePath)

    if "/" in basePath:
        pathSep = "/"
    else:
        pathSep = "\\"
    
    # Generate output folder path
    output_json_path = os.path.join(basePath, 'outputJSON')

    """
        Check if input folder exists, else throw exception
    """
    if(os.path.exists(module_path)):
        filenames = glob.glob(os.path.join(module_path, htmlDocName))

        # Create language specific folder in outputJSON folder if it doesn't exist
        if(not os.path.exists(output_json_path)):
            os.mkdir(output_json_path)
        logger = MatchLogger(f'Parser_{getRandomString(1)}', htmlDocName,
                             domain, procedureType, languageCode, "HTML", fileNameLog)

        styleLogger = MatchLogger(
            f'Style Dictionary_{getRandomString(1)}', htmlDocName, domain, procedureType, languageCode, "HTML", fileNameLog)

        styleRulesObj = StyleRulesDictionary(logger=styleLogger,
                                             controlBasePath=controlBasePath,
                                             language=languageCode,
                                             fileName=fileNameQrd,
                                             domain=domain,
                                             procedureType=procedureType
                                             )

        parserObj = parserExtractor(config, logger, styleRulesObj.styleRuleDict,
                                    styleRulesObj.styleFeatureKeyList,
                                    styleRulesObj.qrd_section_headings)

        for input_filename in filenames:
          # if(input_filename.find('Kalydeco II-86-PI-clean')!=-1):
            output_filename = os.path.join(output_json_path, htmlDocName)
            style_filepath =  output_filename.replace('.html','.txt')
            style_filepath =  style_filepath.replace('.txtl','.txt')
            style_filepath =  style_filepath.replace('.htm','.txt')
            print("-------------",style_filepath,"-----------------")

            output_filename = output_filename.replace('.html', '.json')
            output_filename = output_filename.replace('.htm', '.json')
            print(input_filename, output_filename)
            parserObj.createPIJsonFromHTML(input_filepath=input_filename,
                                           output_filepath=output_filename,
                                           style_filepath = style_filepath,
                                           img_base64_dict=parserObj.convertImgToBase64(input_filename)
                                           )
            
        return output_filename.split(pathSep)[-1], style_filepath
    else:
        try:    
            raise FolderNotFoundError(module_path + " not found")
        except:  
            logger.logFlowCheckpoint("Folder For Language Code Not Found In Input File")
            logger.logException("Folder For Language Code Not Found In Input File")
        raise FolderNotFoundError(module_path + " not found")
        return None


def splitJson(controlBasePath, basePath, domain, procedureType, languageCode, fileNameJson, fileNameQrd, fileNameLog):

    styleLogger = MatchLogger(
        f'Style Dictionary_{getRandomString(1)}', fileNameJson, domain, procedureType, languageCode, "Json", fileNameLog)

    styleRulesObj = StyleRulesDictionary(logger=styleLogger,
                                        controlBasePath=controlBasePath,
                                        language=languageCode,
                                        fileName=fileNameQrd,
                                        domain=domain,
                                        procedureType=procedureType
                                        )
    
    path_json = os.path.join(basePath,'outputJSON', fileNameJson)
    print("PathJson",path_json)
    partitionLogger = MatchLogger(
        f'Partition_{getRandomString(1)}', fileNameJson, domain, procedureType, languageCode, "Json", fileNameLog)

    partitioner = DocTypePartitioner(partitionLogger)

    partitionedJsonPaths = partitioner.partitionHtmls(
        styleRulesObj.qrd_section_headings, path_json)

    return partitionedJsonPaths


def extractAndValidateHeadings(controlBasePath,
                                basePath,
                                domain,
                                procedureType,
                                languageCode,
                                documentNumber,
                                fileNameDoc,
                                fileNameQrd,
                                fileNameMatchRuleBook,
                                fileNameDocumentTypeNames,
                                fileNameLog,
                                stopWordFilterLen=6,
                                isPackageLeaflet=False,
                                medName=None
                                ):

    if documentNumber == 0:
        topHeadingsConsidered = 4
        bottomHeadingsConsidered = 6
    elif documentNumber == 1:
        topHeadingsConsidered = 3
        bottomHeadingsConsidered = 5
    elif documentNumber == 2:
        topHeadingsConsidered = 5
        bottomHeadingsConsidered = 15
    else:
        topHeadingsConsidered = 5
        bottomHeadingsConsidered = 10

    print(f"Starting Heading Extraction For File :- {fileNameDoc}")
    logger = MatchLogger(f"Heading Extraction {fileNameDoc}_{getRandomString(1)}", fileNameDoc, domain, procedureType, languageCode, documentNumber, fileNameLog)
    logger.logFlowCheckpoint("Starting Heading Extraction")

    stopWordlanguage = DocumentTypeNames(
        controlBasePath=controlBasePath,
        fileNameDocumentTypeNames=fileNameDocumentTypeNames,
        languageCode=languageCode,
        domain=domain,
        procedureType=procedureType,
        documentNumber=documentNumber
        ).extractStopWordLanguage()

    matchDocObj = MatchDocument(
        logger,
        controlBasePath,
        basePath,
        domain,
        procedureType,
        languageCode,
        documentNumber,
        fileNameDoc,
        fileNameQrd,
        fileNameMatchRuleBook,
        fileNameDocumentTypeNames,
        topHeadingsConsidered,
        bottomHeadingsConsidered,
        stopWordFilterLen,
        stopWordlanguage,
        isPackageLeaflet,
        medName)
    df, coll, documentType = matchDocObj.matchHtmlHeaddingsWithQrd()

    return df, coll, documentType


def parseDocument(controlBasePath, basePath ,htmlDocName, fileNameQrd, fileNameMatchRuleBook, fileNameDocumentTypeNames, medName = None):
    
    
    if "/" in basePath:
        pathSep = "/"        
    else:
        pathSep = "\\"
    
    fileNameLog = os.path.join(basePath,'FinalLog.txt')

    pathComponents = basePath.split(pathSep)
    print(pathComponents, htmlDocName)
    timestamp = pathComponents[-1]
    languageCode =  pathComponents[-2]
    medName = pathComponents[-3]
    procedureType = pathComponents[-4]
    domain = pathComponents[-5]

    print(timestamp, languageCode, medName, procedureType, domain)
        
    flowLogger =  MatchLogger(f"Flow Logger HTML_{getRandomString(1)}", htmlDocName, domain, procedureType, languageCode, "HTML", fileNameLog)
    
    metrics = Metrics(os.path.join(basePath,'Metrics.csv'),flowLogger)
    
    
    flowLogger.logFlowCheckpoint("Starting HTML Conversion To Json")
    ###Convert Html to Json
    fileNameJson, stylesFilePath = convertHtmlToJson(controlBasePath, basePath, domain, procedureType, languageCode, htmlDocName, fileNameQrd, fileNameLog)
    
    print("stylePath:-",stylesFilePath)
    flowLogger.logFlowCheckpoint("Completed HTML Conversion To Json")
    metrics.getMetric("HTML Conversion To Json")

    flowLogger.logFlowCheckpoint("Starting Json Split")

    ###Split Uber Json to multiple Jsons for each category.
    partitionedJsonPaths = splitJson(controlBasePath, basePath, domain, procedureType, languageCode, fileNameJson, fileNameQrd, fileNameLog)
    
    partitionedJsonPaths = [ path.split(pathSep)[-1] for path in partitionedJsonPaths]
    flowLogger.logFlowCheckpoint(str(partitionedJsonPaths))
    
    flowLogger.logFlowCheckpoint("Completed Json Split")
    metrics.getMetric("Split Json")
    
    flowLogger.logFlowCheckpoint("Started Processing Partitioned Jsons")
    
    for index, fileNamePartitioned in enumerate(partitionedJsonPaths):
        #print("Index", index)
        #if index == 0:
        #    print("Asdddddddddddddddddddddddddd")
        #    continue
        flowLogger.logFlowCheckpoint(f"\n\n\n\n||||||||||||||||||||||||||||||||{str(index)} ||||| {str(fileNamePartitioned)}||||||||||||||||||||||||||||||||\n\n\n\n")
        
        if index == 3:
            stopWordFilterLen = 100
            isPackageLeaflet = True
        else:
            stopWordFilterLen = 6
            isPackageLeaflet = False
            
        df, coll, documentType = extractAndValidateHeadings(controlBasePath,
                                    basePath,
                                    domain,
                                    procedureType,
                                    languageCode,
                                    index,
                                    fileNamePartitioned,
                                    fileNameQrd,
                                    fileNameMatchRuleBook,
                                    fileNameDocumentTypeNames,
                                    fileNameLog,
                                    stopWordFilterLen=stopWordFilterLen,
                                    isPackageLeaflet=isPackageLeaflet,
                                    medName=medName)
        
        
        print(f"Completed Heading Extraction For File")
        flowLogger.logFlowCheckpoint("Completed Heading Extraction For File")
        metrics.getMetric(f"{index}: Heading Extraction")

        print(f"Starting Document Annotation For File :- {fileNamePartitioned}")        
        flowLogger.logFlowCheckpoint("Starting Document Annotation For File")
        documentAnnotationObj = DocumentAnnotation(fileNamePartitioned,'c20835db4b1b4e108828a8537ff41506','https://spor-sit.azure-api.net/pms/api/v2/',df,coll)
        try:
            pms_oms_annotation_data = documentAnnotationObj.processRegulatedAuthorizationForDoc()
            print(pms_oms_annotation_data)
        except:
            pms_oms_annotation_data = None
            print("Error Found")
            
        print(f"Completed Document Annotation")        
        flowLogger.logFlowCheckpoint("Completed Document Annotation")
        metrics.getMetric(f"{index}: Document Annotation")
        
        print(f"Starting Extracting Content Between Heading For File :- {fileNamePartitioned}")        
        flowLogger.logFlowCheckpoint("Starting Extracting Content Between Heading")
        
        extractContentlogger =  MatchLogger(f'ExtractContentBetween_{index}_{getRandomString(1)}', fileNamePartitioned, domain, procedureType, languageCode, index, fileNameLog)
        extractorObj = DataBetweenHeadingsExtractor(extractContentlogger, basePath, coll)
        dfExtractedHierRR = extractorObj.extractContentBetweenHeadings(fileNamePartitioned)
        
        print(f"Completed Extracting Content Between Heading")        
        flowLogger.logFlowCheckpoint("Completed Extracting Content Between Heading")
        metrics.getMetric(f"{index}: Content Extraction")
        
        xmlLogger =  MatchLogger(f'XmlGeneration_{index}_{getRandomString(1)}', fileNamePartitioned, domain, procedureType, languageCode, index, fileNameLog)
        fhirXmlGeneratorObj = FhirXmlGenerator(xmlLogger, controlBasePath, basePath, pms_oms_annotation_data, stylesFilePath, medName)
        fileNameXml = fileNamePartitioned.replace('.json','.xml')
        generatedXml = fhirXmlGeneratorObj.generateXml(dfExtractedHierRR, fileNameXml)
        
        metrics.getMetric(f"{index}: Generate XML")
        
        fhirServiceLogger =  MatchLogger(f'XML Submission Logger_{index}_{getRandomString(1)}', fileNamePartitioned, domain, procedureType, languageCode, index, fileNameLog)

        fhirServiceObj = FhirService(fhirServiceLogger, basePath, generatedXml)
        fhirServiceObj.submitFhirXml()
        
        metrics.getMetric(f"{index}: Submit FHIR Msg")
        
        print(f"Created XML File For :- {fileNamePartitioned}")      
        
        #return df,coll,dfExtractedHierRR
    
    
    flowLogger.logFlowCheckpoint("Completed Processing Partitioned Jsons")
    metrics.getMetric(f"{index}: Completed")
    metrics.end()

C:\Users\vipsharm\AppData\Local\Continuum\anaconda3\lib\site-packages\fuzzywuzzy\fuzz.py:11: UserWarning: Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning
  warnings.warn('Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning')
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\vipsharm\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [3]:
wordToHtmlConvertorObj = WordToHtmlConvertor()
wordToHtmlConvertorObj.convertWordToHTML()

2021-05-19 00:50:50,658 : WordToHtmlLogger_M : Input file: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\Ingest\ABASAGLAR~H~CAP~en.docx | H | CAP |  en | .docx | ABASAGLAR~H~CAP~en.docx
2021-05-19 00:50:50,659 : WordToHtmlLogger_M : Output file: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\ABASAGLAR\en\2021-05-18T19-20-50Z\ABASAGLAR_clean | H | CAP |  en | .docx | ABASAGLAR~H~CAP~en.docx


Word Files in folder:  ['ABASAGLAR~H~CAP~en.docx', 'Abilify Maintena~H~CAP~en.doc', 'ABILIFY~H~CAP~en.doc', 'Adakveo~H~CAP~en.docx', 'Adcetris~H~CAP~en.doc', '~$ilify Maintena~H~CAP~en.doc']
Input file: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\Ingest\ABASAGLAR~H~CAP~en.docx
Output file: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\ABASAGLAR\en\2021-05-18T19-20-50Z\ABASAGLAR_clean


2021-05-19 00:51:09,654 : WordToHtmlLogger_M : Opened file: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\Ingest\ABASAGLAR~H~CAP~en.docx | H | CAP |  en | .docx | ABASAGLAR~H~CAP~en.docx


Opened file: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\data\Ingest\ABASAGLAR~H~CAP~en.docx


2021-05-19 00:51:11,212 : WordToHtmlLogger_M : Starting document cleaning process | H | CAP |  en | .docx | ABASAGLAR~H~CAP~en.docx


...

2021-05-19 00:54:46,529 : WordToHtmlLogger_2 : Completed document cleaning process | H | CAP |  en | .doc | Abilify Maintena~H~CAP~en.doc
2021-05-19 00:54:46,532 : WordToHtmlLogger_2 : Preparing zip file | H | CAP |  en | .doc | Abilify Maintena~H~CAP~en.doc
2021-05-19 00:54:47,821 : WordToHtmlLogger_2 : Zip file created: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\inputblob\Abilify Maintena~H~CAP~en~2021-05-18T19-22-05Z.zip | H | CAP |  en | .doc | Abilify Maintena~H~CAP~en.doc
2021-05-19 00:54:47,825 : WordToHtmlLogger_2 : Uploading to Azure Storage as blob:
	F:\Projects\EMA\Repository\EMA EPI PoC\function_code\inputblob\Abilify Maintena~H~CAP~en~2021-05-18T19-22-05Z.zip | H | CAP |  en | .doc | Abilify Maintena~H~CAP~en.doc



Uploading File to  Azure Storage:
	F:\Projects\EMA\Repository\EMA EPI PoC\function_code\inputblob\Abilify Maintena~H~CAP~en~2021-05-18T19-22-05Z.zip


2021-05-19 00:54:59,563 : WordToHtmlLogger_2 : Uploaded F:\Projects\EMA\Repository\EMA EPI PoC\function_code\inputblob\Abilify Maintena~H~CAP~en~2021-05-18T19-22-05Z.zipsuccessfully | H | CAP |  en | .doc | Abilify Maintena~H~CAP~en.doc
2021-05-19 00:54:59,564 : WordToHtmlLogger_2 : Deleting input word file: Abilify Maintena~H~CAP~en.doc | H | CAP |  en | .doc | Abilify Maintena~H~CAP~en.doc
2021-05-19 00:54:59,573 : WordToHtmlLogger_2 : Killing Word processes as exception was raised | H | CAP |  en | .doc | Abilify Maintena~H~CAP~en.doc


Exception raised
Killing WINWORD.EXE
Killing WINWORD.EXE
Killing WINWORD.EXE
Killing WINWORD.EXE
Killing WINWORD.EXE
Killing WINWORD.EXE
Killing WINWORD.EXE
Killing WINWORD.EXE
Killing WINWORD.EXE
Killing WINWORD.EXE
Killing WINWORD.EXE
Killing WINWORD.EXE


NoSuchProcess: psutil.NoSuchProcess process no longer exists (pid=34304)

In [3]:
# inputZipFolderPath = "F:\Projects\EMA\Repository\EMA EPI PoC\\function_code\\inputblob"
inputZipFolderPath = os.path.abspath(os.path.join('..'))
inputZipFolderPath = os.path.join(inputZipFolderPath, 'inputblob')
inputZipFileName = "Zynteglo~H~CAP~en~2021-05-19T07-52-54Z.zip"

In [4]:
fileNameQrd = 'qrd_canonical_model.csv'
fileNameMatchRuleBook = 'ruleDict.json'
fileNameDocumentTypeNames = 'documentTypeNames.json'
fsMountName = '/mounted'

info = inputZipFileName.split("~")

try:
    medName = info[0]
    domain = info[1]
    procedureType = info[2]
    languageCode = info[3]
    timestamp = info[4]
    timestamp = timestamp.replace(".zip","")

except Exception:
    raise f"Missing required info in the zip file name {inputZipFileName}"

if "\\" in os.getcwd():
    localEnv = True
    inputZipFolderPath = os.path.join(os.path.abspath(os.path.join('..')),inputZipFolderPath)
    outputFolderPath = os.path.join(os.path.abspath(os.path.join('..')), 'work', f"{domain}", f"{procedureType}", f"{medName}", f"{languageCode}", f"{timestamp}")
    controlFolderPath = os.path.join(os.path.abspath(os.path.join('..')),'control')
else:
    localEnv = False
    inputZipFolderPath = os.path.join(f'{fsMountName}',inputZipFolderPath)
    outputFolderPath = os.path.join(f'{fsMountName}', 'work', f"{domain}", f"{procedureType}", f"{medName}", f"{languageCode}", f"{timestamp}")
    controlFolderPath = os.path.join(f'{fsMountName}','control')


print(inputZipFileName, inputZipFolderPath, outputFolderPath, controlFolderPath)

mode = 0o666

if localEnv is True:
    inputZipFolderPath = inputZipFolderPath.replace("/","\\")
    outputFolderPath = outputFolderPath.replace("/","\\")
    controlFolderPath = controlFolderPath.replace("/","\\")

try:
    os.makedirs(inputZipFolderPath, mode)
    os.makedirs(outputFolderPath, mode)
    os.makedirs(controlFolderPath, mode)

except Exception:
    print("Already Present")
    
with zipfile.ZipFile(f'{inputZipFolderPath}/{inputZipFileName}',"r") as zip_ref:
        zip_ref.extractall(outputFolderPath)
    

_,_,fileNames = next(os.walk(outputFolderPath))
htmlFileName = [fileName for fileName in fileNames if ".htm" in fileName][0]

print(htmlFileName)



Zynteglo~H~CAP~en~2021-05-19T07-52-54Z.zip F:\Projects\EMA\Repository\EMA EPI PoC\function_code\inputblob F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\Zynteglo\en\2021-05-19T07-52-54Z F:\Projects\EMA\Repository\EMA EPI PoC\function_code\control
Already Present
Zynteglo_clean.htm


In [30]:
parseDocument(controlFolderPath, outputFolderPath, htmlFileName, fileNameQrd, fileNameMatchRuleBook, fileNameDocumentTypeNames, medName)

2021-05-19 05:08:05,512 : Flow Logger HTML_Z : Starting HTML Conversion To Json | H | CAP |  en | HTML | Zynteglo_clean.htm
2021-05-19 05:08:05,518 : Style Dictionary_Q : Reading style dictionary in file: rule_dictionary_en.json | H | CAP |  en | HTML | Zynteglo_clean.htm
2021-05-19 05:08:05,551 : Style Dictionary_Q : Qrd Section Keys Retrieved For Style Dictionary: ANNEX I, ANNEX II, ANNEX III, B. PACKAGE LEAFLET | H | CAP |  en | HTML | Zynteglo_clean.htm


['F:', 'Projects', 'EMA', 'Repository', 'EMA EPI PoC', 'function_code', 'work', 'H', 'CAP', 'Zynteglo', 'en', '2021-05-19T07-52-54Z'] Zynteglo_clean.htm
2021-05-19T07-52-54Z en Zynteglo CAP H
------------- F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\Zynteglo\en\2021-05-19T07-52-54Z\outputJSON\Zynteglo_clean.txt -----------------
F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\Zynteglo\en\2021-05-19T07-52-54Z\Zynteglo_clean.htm F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\Zynteglo\en\2021-05-19T07-52-54Z\outputJSON\Zynteglo_clean.json


2021-05-19 05:08:05,989 : Parser_q : Style Information Stored In File: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\Zynteglo\en\2021-05-19T07-52-54Z\outputJSON\Zynteglo_clean.txt | H | CAP |  en | HTML | Zynteglo_clean.htm
2021-05-19 05:08:05,989 : Parser_q : Style Information Stored In File: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\Zynteglo\en\2021-05-19T07-52-54Z\outputJSON\Zynteglo_clean.txt | H | CAP |  en | HTML | Zynteglo_clean.htm
2021-05-19 05:08:05,989 : Parser_q : Style Information Stored In File: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\Zynteglo\en\2021-05-19T07-52-54Z\outputJSON\Zynteglo_clean.txt | H | CAP |  en | HTML | Zynteglo_clean.htm
2021-05-19 05:08:08,181 : Parser_q : Writing to file: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\Zynteglo\en\2021-05-19T07-52-54Z\outputJSON\Zynteglo_clean.json | H | CAP |  en | HTML | Zynteglo_clean.htm
2021-05-19 05:08:08,181 : Parser_q : Writing to 

stylePath:- F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\Zynteglo\en\2021-05-19T07-52-54Z\outputJSON\Zynteglo_clean.txt
Metrics : HTML Conversion To Json,0.047 Min,15.175288 MB,35.821356 MB,67.5

PathJson F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\Zynteglo\en\2021-05-19T07-52-54Z\outputJSON\Zynteglo_clean.json


2021-05-19 05:08:08,593 : Partition_U : Writing partition to file: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\Zynteglo\en\2021-05-19T07-52-54Z\partitionedJSONs\Zynteglo_clean_ANNEX III.json | H | CAP |  en | Json | Zynteglo_clean.json
2021-05-19 05:08:08,600 : Partition_U : Writing partition to file: F:\Projects\EMA\Repository\EMA EPI PoC\function_code\work\H\CAP\Zynteglo\en\2021-05-19T07-52-54Z\partitionedJSONs\Zynteglo_clean_ PACKAGE LEAFLET.json | H | CAP |  en | Json | Zynteglo_clean.json
2021-05-19 05:08:08,610 : Flow Logger HTML_Z : ['Zynteglo_clean_SmPC.json', 'Zynteglo_clean_ANNEX II.json', 'Zynteglo_clean_ANNEX III.json', 'Zynteglo_clean_ PACKAGE LEAFLET.json'] | H | CAP |  en | HTML | Zynteglo_clean.htm
2021-05-19 05:08:08,611 : Flow Logger HTML_Z : Completed Json Split | H | CAP |  en | HTML | Zynteglo_clean.htm
2021-05-19 05:08:08,612 : Flow Logger HTML_Z : Started Processing Partitioned Jsons | H | CAP |  en | HTML | Zynteglo_clean.htm
2021-05-19 05:08

...

 dispersion for infusion. ' | Qrd txt :- '6.6 Special precautions for disposal <and other handling>' | Matched :- 'False'0.62| | H | CAP |  en | 0 | Zynteglo_clean_SmPC.json | Doc txt :- 'Zynteglo 1.2‑20 × 106 cells/mL
2021-05-19 05:08:09,724 : Heading Extraction Zynteglo_clean_SmPC.json_h : Match Passed | H | CAP |  en | 0 | Zynteglo_clean_SmPC.json | Doc txt :- '2. QUALITATIVE AND QUANTITATIVE COMPOSITION' | Qrd txt :- '2. QUALITATIVE AND QUANTITATIVE COMPOSITION' | Matched :- 'True'
2021-05-19 05:08:09,733 : Heading Extraction Zynteglo_clean_SmPC.json_h : Validation Passed | H | CAP |  en | 0 | Zynteglo_clean_SmPC.json | currHeadId :- '20004' | prevHeadingCurrId :- '20003' | prevHeadingFoundId :- '20003'
2021-05-19 05:08:09,759 : Heading Extraction Zynteglo_clean_SmPC.json_h : Match Passed | H | CAP |  en | 0 | Zynteglo_clean_SmPC.json | Doc txt :- '2.1 General description' | Qrd txt :- '2.1 General description' | Matched :- 'True'
2021-05-19 05:08:09,768 : Heading Extraction Zynteg


OriginalCheck



2021-05-19 05:08:10,190 : Heading Extraction Zynteglo_clean_SmPC.json_h : Match Passed : <=4|11.11|(95, 89, 95)|0.989| | H | CAP |  en | 0 | Zynteglo_clean_SmPC.json | Doc txt :- 'Excipient with known effect' | Qrd txt :- 'Excipient(s) with known effect' | Matched :- 'True'
2021-05-19 05:08:10,202 : Heading Extraction Zynteglo_clean_SmPC.json_h : Validation Failed As Current H3 Heading Is Not Part Of Valid H3 Headings in Previous H2 | H | CAP |  en | 0 | Zynteglo_clean_SmPC.json | currHeadId :- '20007' | prevHeadingCurrId :- '20006' | prevHeadingFoundId :- '20006'
2021-05-19 05:08:10,854 : Heading Extraction Zynteglo_clean_SmPC.json_h : Match Passed | H | CAP |  en | 0 | Zynteglo_clean_SmPC.json | Doc txt :- '3. PHARMACEUTICAL FORM' | Qrd txt :- '3. PHARMACEUTICAL FORM' | Matched :- 'True'
2021-05-19 05:08:10,866 : Heading Extraction Zynteglo_clean_SmPC.json_h : Validation Flow Is Broken | H | CAP |  en | 0 | Zynteglo_clean_SmPC.json | currHeadId :- '20008' | prevHeadingCurrId :- '' | 

2021-05-19 05:08:14,976 : Heading Extraction Zynteglo_clean_SmPC.json_h : Validation Flow Is Broken | H | CAP |  en | 0 | Zynteglo_clean_SmPC.json | currHeadId :- '20031' | prevHeadingCurrId :- '' | prevHeadingFoundId :- '20011'
2021-05-19 05:08:14,990 : Heading Extraction Zynteglo_clean_SmPC.json_h : Validation Failed As Current H3 Heading Is Not Part Of Valid H3 Headings in Previous H2 | H | CAP |  en | 0 | Zynteglo_clean_SmPC.json | currHeadId :- '20031' | prevHeadingCurrId :- '20011' | prevHeadingFoundId :- '20011'
2021-05-19 05:08:15,009 : Heading Extraction Zynteglo_clean_SmPC.json_h : Match Passed | H | CAP |  en | 0 | Zynteglo_clean_SmPC.json | Doc txt :- 'Paediatric population' | Qrd txt :- 'Paediatric population' | Matched :- 'True'
2021-05-19 05:08:15,020 : Heading Extraction Zynteglo_clean_SmPC.json_h : Validation Flow Is Broken | H | CAP |  en | 0 | Zynteglo_clean_SmPC.json | currHeadId :- '20037' | prevHeadingCurrId :- '' | prevHeadingFoundId :- '20011'
2021-05-19 05:08:1

KeyboardInterrupt: 

In [20]:
a

Bold                        Classes  \
0     True                  ['MsoNormal']   
1    False                  ['MsoNormal']   
2     True                  ['MsoNormal']   
3    False                  ['MsoNormal']   
4     True                  ['MsoNormal']   
5    False                  ['MsoNormal']   
6     True                  ['MsoNormal']   
7    False                  ['MsoNormal']   
8     True                  ['MsoNormal']   
9    False                  ['MsoNormal']   
10    True                  ['MsoNormal']   
11   False                           None   
12   False                           None   
13   False                  ['MsoNormal']   
14    True                  ['MsoNormal']   
15   False                  ['MsoNormal']   
16   False                  ['MsoNormal']   
17   False                  ['MsoNormal']   
18   False                  ['MsoNormal']   
19   False                  ['MsoNormal']   
20   False                  ['MsoNormal']   
21   False                  ['MsoNormal']   
22   False                  ['MsoNormal']   
23   False                  ['MsoNormal']   
24   False                  ['MsoNormal']   
25   False                  ['MsoNormal']   
26   False                  ['MsoNormal']   
27   False                  ['MsoNormal']   
28   False                  ['MsoNormal']   
29   False                  ['MsoNormal']   
30   False                  ['MsoNormal']   
31    True                  ['MsoNormal']   
32   False                  ['MsoNormal']   
33   False                  ['MsoNormal']   
34   False                  ['MsoNormal']   
35   False                  ['MsoNormal']   
36    True                  ['MsoNormal']   
37   False                  ['MsoNormal']   
38    True                  ['MsoNormal']   
39   False                  ['MsoNormal']   
40   False                  ['MsoNormal']   
41   False                  ['MsoNormal']   
42   False                  ['MsoNormal']   
43   False                  ['MsoNormal']   
44   False                  ['MsoNormal']   
45    True                  ['MsoNormal']   
46   False                  ['MsoNormal']   
47    True                  ['MsoNormal']   
48   False                  ['MsoNormal']   
49   False                  ['MsoNormal']   
50   False                  ['MsoNormal']   
51   False                  ['MsoNormal']   
52   False  ['MsoListParagraphCxSpFirst']   
53   False   ['MsoListParagraphCxSpLast']   
54    True                  ['MsoNormal']   
55   False                  ['MsoNormal']   
56   False                  ['MsoNormal']   
57   False                  ['MsoNormal']   
58   False                  ['MsoNormal']   
59   False                  ['MsoNormal']   
60   False                  ['MsoNormal']   
61   False                  ['MsoNormal']   
62   False                  ['MsoNormal']   
63   False                  ['MsoNormal']   
64   False                  ['MsoNormal']   
65   False                  ['MsoNormal']   
66   False                  ['MsoNormal']   
67   False                  ['MsoNormal']   
68   False                  ['MsoNormal']   
69   False                  ['MsoNormal']   
70   False                  ['MsoNormal']   
71   False                  ['MsoNormal']   
72   False                  ['MsoNormal']   
73   False                  ['MsoNormal']   
74   False                  ['MsoNormal']   
75   False                  ['MsoNormal']   
76   False                  ['MsoNormal']   
77   False                  ['MsoNormal']   
78   False                  ['MsoNormal']   
79   False                  ['MsoNormal']   
80   False                  ['MsoNormal']   
81   False                  ['MsoNormal']   
82   False                  ['MsoNormal']   
83   False                  ['MsoNormal']   
84   False                  ['MsoNormal']   
85   False                  ['MsoNormal']   
86   False                  ['MsoNormal']   
87   False                  ['MsoNormal']   
8

In [14]:
convertCollectionToDataFrame(b)

index     id Procedure type Display code  \
0     680  20001            CAP          NaN   
1     682  20003            CAP            1   
2     683  20004            CAP            2   
3     684  20005            CAP          2.1   
4     685  20006            CAP          2.2   
5     686  20007            CAP          NaN   
6     687  20008            CAP            3   
7     688  20009            CAP            4   
8     689  20010            CAP          4.1   
9     690  20011            CAP          4.2   
10    691  20012            CAP          NaN   
11    692  20013            CAP          NaN   
12    693  20014            CAP          NaN   
13    695  20016            CAP          4.3   
14    696  20017            CAP          4.4   
15    697  20018            CAP          NaN   
16    699  20020            CAP          4.5   
17    701  20022            CAP          4.6   
18    702  20023            CAP          NaN   
19    703  20024            CAP          NaN   
20    704  20025            CAP          NaN   
21    705  20026            CAP          4.7   
22    706  20027            CAP          4.8   
23    707  20028            CAP          NaN   
24    708  20029            CAP          NaN   
25    709  20030            CAP          4.9   
26    711  20032            CAP            5   
27    712  20033            CAP          5.1   
28    713  20034            CAP          NaN   
29    714  20035            CAP          NaN   
30    716  20037            CAP          NaN   
31    717  20038            CAP          5.2   
32    724  20045            CAP          5.3   
33    726  20047            CAP            6   
34    727  20048            CAP          6.1   
35    728  20049            CAP          6.2   
36    729  20050            CAP          6.3   
37    730  20051            CAP          6.4   
38    731  20052            CAP          6.5   
39    732  20053            CAP          6.6   
40    734  20055            CAP            7   
41    735  20056            CAP            8   
42    736  20057            CAP            9   
43    737  20058            CAP           10   

                                                                                               Name  \
0                                                                SUMMARY OF PRODUCT CHARACTERISTICS   
1                                                                     NAME OF THE MEDICINAL PRODUCT   
2                                                          QUALITATIVE AND QUANTITATIVE COMPOSITION   
3                                                                               General description   
4                                                          Qualitative and quantitative composition   
5                                                                    Excipient(s) with known effect   
6                                                                               PHARMACEUTICAL FORM   
7                                                                              CLINICAL PARTICULARS   
8                                                                           Therapeutic indications   
9                                                             Posology and method of administration   
10                                                                                         Posology   
11                                                                            Paediatric population   
12                                                                        Method of administration    
13                                                                                Contraindications   
14                                                         Special warnings and precautions for use   
15                                                                                     Traceability   
16                         Interaction with other medicinal products and other forms of inte

In [28]:
dfCanonicalModel = pd.read_csv(f'{controlFolderPath}\\qrdTemplate\\{fileNameQrd}', encoding= 'utf-8')

colsofInterest  = ['id','domain','Procedure type', 'Document type', 'Language code',
'Display code', 'Name', 'parent_id', 'Mandatory','heading_id']

dfCanonicalModel = dfCanonicalModel[colsofInterest]
dfCanonicalModel['document_number'] = None

dfCanonicalModel

id domain Procedure type                              Document type  \
0          1      H            CAP                                       SmPC   
1          2      H            CAP                                       SmPC   
2          3      H            CAP                                       SmPC   
3          4      H            CAP                                       SmPC   
4          5      H            CAP                                       SmPC   
5          6      H            CAP                                       SmPC   
6          7      H            CAP                                       SmPC   
7          8      H            CAP                                       SmPC   
8          9      H            CAP                                       SmPC   
9         10      H            CAP                                       SmPC   
10        11      H            CAP                                       SmPC   
11        12      H            CAP                                       SmPC   
12        13      H            CAP                                       SmPC   
13        14      H            CAP                                       SmPC   
14        15      H            CAP                                       SmPC   
15        16      H            CAP                                       SmPC   
16        17      H            CAP                                       SmPC   
17        18      H            CAP                                       SmPC   
18        19      H            CAP                                       SmPC   
19        20      H            CAP                                       SmPC   
20        21      H            CAP                                       SmPC   
21        22      H            CAP                                       SmPC   
22        23      H            CAP                                       SmPC   
23        24      H            CAP                                       SmPC   
24        25      H            CAP                                       SmPC   
25        26      H            CAP                                       SmPC   
26        27      H            CAP                                       SmPC   
27        28      H            CAP                                       SmPC   
28        29      H            CAP                                       SmPC   
29        30      H            CAP                                       SmPC   
30        31      H            CAP                                       SmPC   
31        32      H            CAP                                       SmPC   
32        33      H            CAP                                       SmPC   
33        34      H            CAP                                       SmPC   
34        35      H            CAP                                       SmPC   
35        36      H            CAP                                       SmPC   
36        37      H            CAP                                       SmPC   
37        38      H            CAP                                       SmPC   
38        39      H            CAP                                       SmPC   
39        40      H            CAP                                       SmPC   
40        41      H            CAP                                       SmPC   
41        42      H            CAP                                       SmPC   
42        43      H            CAP                                       SmPC   
43        44      H            CAP                                       SmPC   
44        45      H            CAP                                       SmPC   
45        46      H            CAP                                       SmPC   
46        47      H            CAP                                       SmPC   
47        48      H            CAP                                       SmPC   
48        49      H            CAP       

In [22]:
dfCanonicalModel['']
display(dfCanonicalModel[(dfCanonicalModel['Document type'] == 'SmPC')][(dfCanonicalModel['Language code'] == 'en')])


C:\Users\vipsharm\AppData\Local\Continuum\anaconda3\lib\site-packages\ipykernel_launcher.py:2: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  


id domain Procedure type Document type Language code Display code  \
680    20001      H            CAP          SmPC            en          NaN   
681    20002      H            CAP          SmPC            en          NaN   
682    20003      H            CAP          SmPC            en            1   
683    20004      H            CAP          SmPC            en            2   
684    20005      H            CAP          SmPC            en          2.1   
685    20006      H            CAP          SmPC            en          2.2   
686    20007      H            CAP          SmPC            en          NaN   
687    20008      H            CAP          SmPC            en            3   
688    20009      H            CAP          SmPC            en            4   
689    20010      H            CAP          SmPC            en          4.1   
690    20011      H            CAP          SmPC            en          4.2   
691    20012      H            CAP          SmPC            en          NaN   
692    20013      H            CAP          SmPC            en          NaN   
693    20014      H            CAP          SmPC            en          NaN   
694    20015      H            CAP          SmPC            en          NaN   
695    20016      H            CAP          SmPC            en          4.3   
696    20017      H            CAP          SmPC            en          4.4   
697    20018      H            CAP          SmPC            en          NaN   
698    20019      H            CAP          SmPC            en          NaN   
699    20020      H            CAP          SmPC            en          4.5   
700    20021      H            CAP          SmPC            en          NaN   
701    20022      H            CAP          SmPC            en          4.6   
702    20023      H            CAP          SmPC            en          NaN   
703    20024      H            CAP          SmPC            en          NaN   
704    20025      H            CAP          SmPC            en          NaN   
705    20026      H            CAP          SmPC            en          4.7   
706    20027      H            CAP          SmPC            en          4.8   
707    20028      H            CAP          SmPC            en          NaN   
708    20029      H            CAP          SmPC            en          NaN   
709    20030      H            CAP          SmPC            en          4.9   
710    20031      H            CAP          SmPC            en          NaN   
711    20032      H            CAP          SmPC            en            5   
712    20033      H            CAP          SmPC            en          5.1   
713    20034      H            CAP          SmPC            en          NaN   
714    20035      H            CAP          SmPC            en          NaN   
715    20036      H            CAP          SmPC            en          NaN   
716    20037      H            CAP          SmPC            en          NaN   
717    20038      H            CAP          SmPC            en          5.2   
718    20039      H            CAP          SmPC            en          NaN   
719    20040      H            CAP          SmPC            en          NaN   
720    20041      H            CAP          SmPC            en          NaN   
721    20042      H            CAP          SmPC            en          NaN   
722    20043      H            CAP          SmPC            en          NaN   
723    20044      H            CAP          SmPC            en          NaN   
724    20045      H            CAP          SmPC            en          5.3   
725    20046      H            CAP          SmPC            en          NaN   
726    20047      H            CAP          SmPC            en            6   
727    20048      H            CAP          SmPC            en          6.1   
728    20049      H            CAP          SmPC            en          6.2   
729    20050      H            CAP          SmPC            

In [29]:
dfCanonicalModel['document_number'] = self.documentNumber if dfCanonicalModel['Document type'] == 'SmPC' else None

ValueError: The truth value of a Series is ambiguous. Use a.empty, a.bool(), a.item(), a.any() or a.all().